# PreSPI DB Guide

### How to access PreSPI db file

You can extract data as sqlite3 db file from PreSPI app.  
You can the contents by using SQLite DB viewer such as 'DB Browser for SQLite'.  
There are `Acc`, `Gyro`, `Baro`, `Loc`, `Rss` tables.

**indoor or outdoor** → `Loc` (Since we only collect fused locations, impossible for now)  
**floor** → `Baro` (hard)  
**moving or not** → `Acc`  
**Max RSSI** → `Rss` for 2 people  
**contact time** → time when score > 0  
**direct or indirect contact** → time diff when score > 0

In python, you can use `sqlite3` library to access as below.

In [1]:
import sqlite3


db_filename = 'BlackBox/BlackBox_for_instruction.db'
conn = sqlite3.connect(db_filename)
cur = conn.cursor()

In [3]:
tmp = dict()

cur.execute("select * from Rss")
rows = cur.fetchall()
for row in rows:
    elem = {
        'timeMicros': row[1],
        'ssid': row[2],
        'bssid': row[3],
        'freq': row[4],
        'rss': row[5]
    }
    try:
        tmp[row[6]].append(elem)
    except KeyError:
        tmp[row[6]] = [elem]

fp_list = [{'logTime': k, 'data': tmp[k]} for k in sorted(tmp)]

fp_list

[{'logTime': 1599470261033,
  'data': [{'timeMicros': 699206307,
    'ssid': 'HCIL',
    'bssid': '6c:70:9f:e0:92:7e',
    'freq': 2432,
    'rss': -35},
   {'timeMicros': 699206351,
    'ssid': 'ISILAB_2',
    'bssid': '2c:56:dc:84:dd:88',
    'freq': 2462,
    'rss': -46},
   {'timeMicros': 699206304,
    'ssid': 'Lapras2.4G-guest',
    'bssid': '62:38:e0:bb:ee:01',
    'freq': 2437,
    'rss': -47},
   {'timeMicros': 699206334,
    'ssid': 'Lapras2.4G',
    'bssid': '60:38:e0:bb:ee:01',
    'freq': 2437,
    'rss': -49},
   {'timeMicros': 699206233,
    'ssid': 'KEAI',
    'bssid': '18:31:bf:46:ff:d8',
    'freq': 2417,
    'rss': -50},
   {'timeMicros': 699206368,
    'ssid': 'naorobot',
    'bssid': '00:26:66:69:c8:e8',
    'freq': 2462,
    'rss': -50},
   {'timeMicros': 699206338,
    'ssid': 'hcil_vr4t',
    'bssid': '72:5d:cc:48:5b:28',
    'freq': 2447,
    'rss': -53},
   {'timeMicros': 699206375,
    'ssid': 'DioOpenWrt',
    'bssid': '10:6f:3f:e7:f2:84',
    'freq': 2462,


In [3]:
loc_list = list()
cur.execute("select * from Loc")
rows = cur.fetchall()
for row in rows:
    elem = {
        'timeMillis': row[1],  # timestamp from the app
        'givenTimeMillis': row[2],  # timestamp from Location Provider
        'lat': row[3],
        'lon': row[4],
        'alt': row[5],
        'hAcc': row[6],
        'vAcc': row[7],
        'provider': row[8]
    }
    loc_list.append(elem)

If you collect data with 6 seconds interval, currently `Acc`, `Gyro`, `Baro` data may not be exactly distinguished.

In [4]:
acc_list = list()
cur.execute("select * from Acc")
rows = cur.fetchall()
prev_t = -1e8
for row in rows:
    elem = {
        'timeMillis': row[1],
        'timeNanos': row[2],
        'x': row[3],
        'y': row[4],
        'z': row[5]
    }
    if (row[1] - prev_t) < 600:
        acc_list[-1].append(elem)
    else:
        acc_list.append([elem])
    prev_t = row[1]

In [5]:
gyro_list = list()
cur.execute("select * from Gyro")
rows = cur.fetchall()
prev_t = -1e8
for row in rows:
    elem = {
        'timeMillis': row[1],
        'timeNanos': row[2],
        'x': row[3],
        'y': row[4],
        'z': row[5]
    }
    if (row[1] - prev_t) < 600:
        gyro_list[-1].append(elem)
    else:
        gyro_list.append([elem])
    prev_t = row[1]

In [6]:
baro_list = list()
cur.execute("select * from Baro")
rows = cur.fetchall()
prev_t = -1e8
for row in rows:
    elem = {
        'timeMillis': row[1],
        'timeNanos': row[2],
        'value': row[3]
    }
    if (row[1] - prev_t) < 600:
        baro_list[-1].append(elem)
    else:
        baro_list.append([elem])
    prev_t = row[1]

You should close the connection after the task.

In [7]:
conn.close()

### How to upload PreSPI data

You can upload your PreSPI data at [PreSPI Console](http://143.248.53.196:8000/)(ID: admin, PW: isilab123).  
Only `Loc` and `Rss` data are uploaded.

`확진자 관리` → `확진자 추가`

### How to access our mongodb

In python, you can use `pymongo` library to access as below.

In [8]:
from pymongo import MongoClient


client = MongoClient('mongodb://143.248.53.196:19191')  # IP & port number
db = client['kaisq']  # name of DB

Uploaded PreSPI data are stored in `patient` collection.

Example of listing registered patients:

In [9]:
for patient in db['patient'].find({}, limit=5):
    print(patient['code'])

24463856
28277672
38876039
90210623
50460317


Example of accessing a patient's data:

In [10]:
patient_id = db['patient'].find_one({'code': '24463856'})['_id']
wifi_data = [elem for elem in db['record_wifi'].find({'patient': patient_id})]
print(len(wifi_data))

16281


You should close the connection after the task.

In [11]:
client.close()